Instalando Pacote

In [1]:
!git clone https://github.com/huggingface/transformers;
!cd transformers; pip3 install .

Cloning into 'transformers'...
remote: Enumerating objects: 159704, done.
remote: Counting objects: 100% (1156/1156), done.
remote: Compressing objects: 100% (683/683), done.
remote: Total 159704 (delta 617), reused 674 (delta 384), pack-reused 158548
Receiving objects: 100% (159704/159704), 161.18 MiB | 19.66 MiB/s, done.
Resolving deltas: 100% (119651/119651), done.
Processing /content/transformers
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 294.9/294.9 kB 4.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.8/3.8 MB 18.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 28.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 32.8 MB/s eta 0:00:00
  Created wheel for transformers: filename=transformers-4.34.0.dev0-py3-none-any.whl size=7700260 sha256=24d0f6f64489707d9c40492b29fd7b6a7aa4

In [2]:
! pip install simpletransformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 250.8/250.8 kB 3.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 519.6/519.6 kB 7.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 4.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 14.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.1/8.1 MB 31.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 47.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 189.5/189.5 kB 21.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.8/224.8 kB 23.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 15.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 18.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 15.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [3]:
! pip install datasets

Puxando Dataset de Discurso de Ódio

In [4]:
from google.colab import drive
drive.mount('drive')

Mounted at drive


In [5]:
import pandas as pd
import transformers
from transformers import AutoModel, BertTokenizerFast
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
from transformers import AdamW
import tensorflow as tf
import numpy as np
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from sklearn.metrics import accuracy_score, f1_score
from sklearn.utils.class_weight import compute_class_weight
from sklearn.linear_model import SGDClassifier
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import CountVectorizer



# link: https://huggingface.co/datasets/ag_news

In [6]:
test = pd.read_csv('/content/drive/My Drive/Colab Notebooks/t5_key_text/original/base_offensive_test.csv', sep = ';', decimal = ',')
test.head()

text  label
0  #ibelieveblaseyford is liar she is fat ugly li...      1
1  @user @user @user I got in a pretty deep debat...      0
2  ...if you want more shootings and more death, ...      0
3  Angels now have 6 runs. Five of them have come...      0
4  #Travel #Movies and Unix #Fortune combined  Vi...      0

In [7]:
# X_train = dataset['train']['text']
X_test = test['text']
# y_train = dataset['train']['label']
y_test = test['label']

In [8]:
nclasses = len(np.unique(y_test))

In [9]:
nclasses

2

In [10]:
def puxa_dados_normal(caminho):
  csv = pd.read_csv(caminho, sep = ';', decimal = ',')
  original = csv[['texto', 'label']].copy()
  original = original.drop_duplicates()

  # csv = csv[csv['similiaridade_parafrase'] >= 0.95].copy()


  parafrase = csv[['generated', 'label']].copy()
  parafrase = parafrase.drop_duplicates()
  parafrase = parafrase[~(parafrase['generated'].isnull())].copy()
  parafrase.rename(columns={"generated": "texto"}, inplace = True)

  fim = original.append(parafrase)

  fim = fim.sample(frac=1)

  X = fim['texto'].values
  y = fim['label'].values


  return X, y


In [11]:
def puxa_original(caminho):
  csv = pd.read_csv(caminho, sep = ';', decimal = ',')

  X = csv['texto'].values
  y = csv['label'].values


  return X, y

In [12]:
def puxa_dados_normal_pkl(caminho):
  csv = pd.read_pickle(caminho)
  original = csv[['texto', 'label']].copy()
  original = original.drop_duplicates()

  # csv = csv[csv['similiaridade_parafrase'] >= 0.95].copy()


  parafrase = csv[['generated', 'label']].copy()
  # parafrase = parafrase.drop_duplicates()
  parafrase = parafrase[~(parafrase['generated'].isnull())].copy()
  parafrase.rename(columns={"generated": "texto"}, inplace = True)

  fim = original.append(parafrase)

  fim = fim.sample(frac=1)

  X = fim['texto'].values
  y = fim['label'].values


  return X, y


In [13]:
def puxa_dados_lambada(caminho, original):
  csv = pd.read_csv(caminho, sep = ';', decimal = ',')
  original = pd.read_csv(original, sep = ';', decimal = ',')

  # csv = csv[csv['similiaridade_parafrase'] >= 0.95].copy()


  parafrase = csv[['generated', 'new_label']].copy()
  # parafrase = parafrase.drop_duplicates()
  parafrase = parafrase[~(parafrase['generated'].isnull())].copy()
  parafrase.rename(columns={"generated": "texto", "new_label": "label"}, inplace = True)

  fim = original.append(parafrase)

  fim = fim.sample(frac=1)

  X = fim['texto'].values
  y = fim['label'].values


  return X, y

In [14]:
def puxa_dados_lambada_filtro(caminho, original, limiar):
  csv = pd.read_csv(caminho, sep = ';', decimal = ',')
  original = pd.read_csv(original, sep = ';', decimal = ',')

  csv = csv[csv['prob_text'] >= limiar].copy()


  parafrase = csv[['generated', 'new_label']].copy()
  parafrase = parafrase.drop_duplicates()
  parafrase = parafrase[~(parafrase['generated'].isnull())].copy()
  parafrase.rename(columns={"generated": "texto", "new_label": "label"}, inplace = True)

  fim = original.append(parafrase)

  fim = fim.sample(frac=1)

  X = fim['texto'].values
  y = fim['label'].values


  return X, y

In [15]:
def puxa_dados_lambada_pkl_filtro(caminho, original, limiar):
  csv = pd.read_pickle(caminho)
  original = pd.read_csv(original, sep = ';', decimal = ',')

  csv = csv[csv['prob_text'] >= limiar].copy()


  parafrase = csv[['generated', 'new_label']].copy()
  parafrase = parafrase.drop_duplicates()
  parafrase = parafrase[~(parafrase['generated'].isnull())].copy()
  parafrase.rename(columns={"generated": "texto", "new_label": "label"}, inplace = True)

  fim = original.append(parafrase)

  fim = fim.sample(frac=1)

  X = fim['texto'].values
  y = fim['label'].values


  return X, y

In [16]:
def desempenho_LSTM(X_train, X_test, y_train, y_test, classes, num_epochs ):


  # vocab_size = 10000
  embedding_dim = 300
  max_length = 128
  trunc_type = 'post'
  padding_type = 'post'
  oov_tok = '<OOV>'

  tokenizer = Tokenizer( oov_token=oov_tok)
  tokenizer.fit_on_texts(X_train)
  word_index = tokenizer.word_index
  vocab_size = len(word_index)+1

  train_sequences = tokenizer.texts_to_sequences(X_train)
  # val_sequences = tokenizer.texts_to_sequences(X_val)

  train_padded = pad_sequences(train_sequences, maxlen=max_length, padding=padding_type, truncating=trunc_type)
  # val_padded = pad_sequences(val_sequences, maxlen=max_length, padding=padding_type, truncating=trunc_type)

  # model = tf.keras.Sequential([
  #   # Camada Embedding (reduzir dimensionalidade)
  #   tf.keras.layers.Embedding(vocab_size, embedding_dim),
  #   # Camada de LSTM bidirecional
  #   tf.keras.layers.LSTM(embedding_dim),
  #   # Camada densa com Relu
  #   tf.keras.layers.Dense(embedding_dim, activation='relu'),
  #   #Camada de saída para as 4 classes
  #   tf.keras.layers.Dense(classes, activation='softmax')
  #   ])
  model = tf.keras.models.Sequential([
        tf.keras.layers.Embedding(input_dim=vocab_size,
                                  mask_zero= True,
                                  output_dim=embedding_dim,
                                  input_length=max_length,
                                  input_shape=(max_length, )),

        tf.keras.layers.Bidirectional(tf.keras.layers.LSTM(32, return_sequences=True)),
        tf.keras.layers.Bidirectional(tf.keras.layers.LSTM(32, return_sequences=False)),
        tf.keras.layers.Dense(64, activation='relu'),
        tf.keras.layers.Dropout(0.5),
        tf.keras.layers.Dense(units=classes, activation='softmax')
    ])
  # model = tf.keras.Sequential()
  # model.add(tf.keras.layers.Embedding(vocab_size, embedding_dim))
  # model.add(tf.keras.layers.Conv1D(filters=32, kernel_size=3, padding='same', activation='relu'))
  # model.add(tf.keras.layers.MaxPooling1D(pool_size=2))
  # model.add(tf.keras.layers.LSTM(100))
  # model.add(tf.keras.layers.Dense(classes, activation='softmax'))

  model.compile(loss='sparse_categorical_crossentropy', optimizer='adam', metrics=['accuracy'])


  history = model.fit(train_padded, y_train, epochs=num_epochs, verbose=2)

  test_sequences = tokenizer.texts_to_sequences(X_test)
  test_padded = pad_sequences(test_sequences, maxlen=max_length, padding=padding_type, truncating=trunc_type)


  preds_log = model.predict(test_padded)
  preds = tf.argmax(preds_log, 1)
  acc = accuracy_score(y_test, preds)
  f1 = f1_score(y_test, preds, average='macro')

  return acc, f1







In [17]:
def desempenho_CNN(X_train, X_test, y_train, y_test, classes, num_epochs ):


  # vocab_size = 10000
  embedding_dim = 300
  max_length = 128
  trunc_type = 'post'
  padding_type = 'post'
  oov_tok = '<OOV>'

  tokenizer = Tokenizer( oov_token=oov_tok)
  tokenizer.fit_on_texts(X_train)
  word_index = tokenizer.word_index
  vocab_size = len(word_index)+1

  train_sequences = tokenizer.texts_to_sequences(X_train)
  # val_sequences = tokenizer.texts_to_sequences(X_val)

  train_padded = pad_sequences(train_sequences, maxlen=max_length, padding=padding_type, truncating=trunc_type)
  # val_padded = pad_sequences(val_sequences, maxlen=max_length, padding=padding_type, truncating=trunc_type)

  # model = tf.keras.Sequential([
  #   # Camada Embedding (reduzir dimensionalidade)
  #   tf.keras.layers.Embedding(vocab_size, embedding_dim),
  #   # Camada de LSTM bidirecional
  #   tf.keras.layers.LSTM(embedding_dim),
  #   # Camada densa com Relu
  #   tf.keras.layers.Dense(embedding_dim, activation='relu'),
  #   #Camada de saída para as 4 classes
  #   tf.keras.layers.Dense(classes, activation='softmax')
  #   ])
  model = tf.keras.models.Sequential([
        tf.keras.layers.Embedding(input_dim=vocab_size,
                                  mask_zero= True,
                                  output_dim=embedding_dim,
                                  input_length=max_length,
                                  input_shape=(max_length, )),

        tf.keras.layers.Conv1D(filters=100, kernel_size = 3, activation = 'relu',
                               # set 'axis' value to the first and second axis of conv1D weights (rows, cols)
                               kernel_constraint= MaxNorm( max_value=3, axis=[0,1])),

        tf.keras.layers.MaxPool1D(2),
        tf.keras.layers.Flatten(),
        tf.keras.layers.Dropout(0.5),
        tf.keras.layers.Dense(10, activation='relu',
                              # set axis to 0 to constrain each weight vector of length (input_dim,) in dense layer
                              kernel_constraint = MaxNorm( max_value=3, axis=0)),
        tf.keras.layers.Dropout(0.5),
        tf.keras.layers.Dense(units=classes, activation='softmax')
    ])
  # model = tf.keras.Sequential()
  # model.add(tf.keras.layers.Embedding(vocab_size, embedding_dim))
  # model.add(tf.keras.layers.Conv1D(filters=32, kernel_size=3, padding='same', activation='relu'))
  # model.add(tf.keras.layers.MaxPooling1D(pool_size=2))
  # model.add(tf.keras.layers.LSTM(100))
  # model.add(tf.keras.layers.Dense(classes, activation='softmax'))

  model.compile(loss='sparse_categorical_crossentropy', optimizer='adam', metrics=['accuracy'])


  history = model.fit(train_padded, y_train, epochs=num_epochs, verbose=2)

  test_sequences = tokenizer.texts_to_sequences(X_test)
  test_padded = pad_sequences(test_sequences, maxlen=max_length, padding=padding_type, truncating=trunc_type)


  preds_log = model.predict(test_padded)
  preds = tf.argmax(preds_log, 1)
  acc = accuracy_score(y_test, preds)
  f1 = f1_score(y_test, preds, average='macro')

  return acc, f1







In [18]:
# Evaluate the model
from sklearn.metrics import f1_score, accuracy_score

def f1_multiclass(labels, preds):
      return f1_score(labels, preds, average='macro')


In [19]:
def desempenho_transformers(X_train, X_test, y_train, y_test,classes, model,type_model, epochs, batch, max_len):
  from simpletransformers.classification import ClassificationModel
  import pandas as pd
  import logging
  import sklearn

  train_df = pd.DataFrame(X_train)
  train_df['target'] = y_train

  eval_df = pd.DataFrame(X_test)
  eval_df['target'] = y_test



  # Create a ClassificationModel
  model = ClassificationModel(type_model, model, num_labels=classes, args={'num_train_epochs':epochs,
                                                                           'train_batch_size':batch,
                                                                           'max_seq_length':max_len,
                                                                          #  "fp16":False,
                                                                           'overwrite_output_dir': True})

  # Train the model
  model.train_model(train_df)
  result, model_outputs, wrong_predictions = model.eval_model(eval_df, acc=sklearn.metrics.accuracy_score,f1=f1_multiclass)

  return result['acc'], result['f1']





In [20]:

y_test = np.array(y_test)


# Original

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_original(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 4, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  4, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  4, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/170 [00:00<?, ?it/s]

Epoch:   0%|          | 0/4 [00:00<?, ?it/s]

...

Running Epoch 3 of 4:   0%|          | 0/6 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/860 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/108 [00:00<?, ?it/s]

Roberta
ACC:0.7209302325581395
F1:0.4189189189189189


In [ ]:
data = {'Aug': [ 'original1', 'original2', 'original3', 'original4','original5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  original1   0.72093  0.418919   0.720930  0.418919      0.72093    0.418919
1  original2   0.72093  0.418919   0.722093  0.442557      0.72093    0.418919
2  original3   0.72093  0.418919   0.708140  0.418404      0.72093    0.418919
3  original4   0.72093  0.418919   0.720930  0.418919      0.72093    0.418919
4  original5   0.72093  0.418919   0.718605  0.567800      0.72093    0.418919

In [ ]:
base_resultados.describe()

BERT_ACC       BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC    ROBERTA_F1
count   5.00000  5.000000e+00   5.000000  5.000000      5.00000  5.000000e+00
mean    0.72093  4.189189e-01   0.718140  0.453320      0.72093  4.189189e-01
std     0.00000  6.206335e-17   0.005732  0.064822      0.00000  6.206335e-17
min     0.72093  4.189189e-01   0.708140  0.418404      0.72093  4.189189e-01
25%     0.72093  4.189189e-01   0.718605  0.418919      0.72093  4.189189e-01
50%     0.72093  4.189189e-01   0.720930  0.418919      0.72093  4.189189e-01
75%     0.72093  4.189189e-01   0.720930  0.442557      0.72093  4.189189e-01
max     0.72093  4.189189e-01   0.722093  0.567800      0.72093  4.189189e-01

# ProtAugment

In [21]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/protaugment/base_offensive_'+str(perc)+'_protaugment'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/protaugment/base_offensive_'+str(perc)+'_protaugment'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/protaugment/base_offensive_'+str(perc)+'_protaugment'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/protaugment/base_offensive_'+str(perc)+'_protaugment'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/protaugment/base_offensive_'+str(perc)+'_protaugment'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_normal(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 4, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet', 4, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  4, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-10-a91fedf45f9b>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Loading the tokenizer from the `special_tokens_map.json` and the `added_tokens.json` will be removed in `transformers 5`,  it is kept for forward compatibility, but it is recommended to update your `tokenizer_config.json` by uploading it again. You will see the new `added_tokens_decoder` attribute that will store the relevant information.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/957 [00:00<?, ?it/s]

...

Running Epoch 3 of 4:   0%|          | 0/30 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/860 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/108 [00:00<?, ?it/s]

Roberta
ACC:0.7883720930232558
F1:0.703560606060606


In [22]:
data = {'Aug': [ 'eda1', 'eda2', 'eda3', 'eda4','eda5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [23]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.746744  0.666323   0.739070  0.635036     0.777442    0.706166
std    0.031625  0.023393   0.029970  0.100970     0.040302    0.032482
min    0.717442  0.633805   0.711628  0.458482     0.733721    0.669541
25%    0.717442  0.656187   0.719767  0.658198     0.736047    0.679588
50%    0.741860  0.667193   0.720930  0.669231     0.788372    0.703561
75%    0.767442  0.678410   0.767442  0.674650     0.813953    0.738481
max    0.789535  0.696019   0.775581  0.714618     0.815116    0.739657

# EDA

In [24]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/eda/base_offensive_'+str(perc)+'_eda'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/eda/base_offensive_'+str(perc)+'_eda'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/eda/base_offensive_'+str(perc)+'_eda'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/eda/base_offensive_'+str(perc)+'_eda'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/eda/base_offensive_'+str(perc)+'_eda'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_normal(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 1, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  1, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  1, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-10-a91fedf45f9b>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/850 [00:00<?, ?it/s]

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/27 [00:00<?, ?it/s]

...

Running Epoch 0 of 1:   0%|          | 0/27 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/860 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/108 [00:00<?, ?it/s]

Roberta
ACC:0.7209302325581395
F1:0.4189189189189189


In [25]:
data = {'Aug': [ 'eda1', 'eda2', 'eda3', 'eda4','eda5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [26]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  eda1  0.720930  0.418919   0.653488  0.577865      0.72093    0.418919
1  eda2  0.733721  0.495438   0.719767  0.437892      0.72093    0.418919
2  eda3  0.720930  0.418919   0.680233  0.462977      0.72093    0.418919
3  eda4  0.720930  0.418919   0.720930  0.418919      0.72093    0.418919
4  eda5  0.720930  0.418919   0.680233  0.539861      0.72093    0.418919

In [27]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC    ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000      5.00000  5.000000e+00
mean   0.723488  0.434223   0.690930  0.487503      0.72093  4.189189e-01
std    0.005720  0.034221   0.028993  0.068325      0.00000  6.206335e-17
min    0.720930  0.418919   0.653488  0.418919      0.72093  4.189189e-01
25%    0.720930  0.418919   0.680233  0.437892      0.72093  4.189189e-01
50%    0.720930  0.418919   0.680233  0.462977      0.72093  4.189189e-01
75%    0.720930  0.418919   0.719767  0.539861      0.72093  4.189189e-01
max    0.733721  0.495438   0.720930  0.577865      0.72093  4.189189e-01

# SSMBA

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/ssmba/base_offensive_'+str(perc)+'_ssmba'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/ssmba/base_offensive_'+str(perc)+'_ssmba'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/ssmba/base_offensive_'+str(perc)+'_ssmba'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/ssmba/base_offensive_'+str(perc)+'_ssmba'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/ssmba/base_offensive_'+str(perc)+'_ssmba'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_normal(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 1, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  1, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  1, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-10-a91fedf45f9b>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/1020 [00:00<?, ?it/s]

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/32 [00:00<?, ?it/s]

...

Running Epoch 0 of 1:   0%|          | 0/32 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/860 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/108 [00:00<?, ?it/s]

Roberta
ACC:0.7209302325581395
F1:0.4189189189189189


In [ ]:
data = {'Aug': [ 'eda1', 'eda2', 'eda3', 'eda4','eda5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  eda1  0.724419  0.447221   0.717442  0.436941      0.72093    0.418919
1  eda2  0.720930  0.418919   0.710465  0.470421      0.72093    0.418919
2  eda3  0.723256  0.551707   0.720930  0.418919      0.72093    0.418919
3  eda4  0.746512  0.564470   0.701163  0.620235      0.72093    0.418919
4  eda5  0.738372  0.495030   0.746512  0.566705      0.72093    0.418919

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC    ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000      5.00000  5.000000e+00
mean   0.730698  0.495469   0.719302  0.502644      0.72093  4.189189e-01
std    0.011171  0.063466   0.016982  0.087029      0.00000  6.206335e-17
min    0.720930  0.418919   0.701163  0.418919      0.72093  4.189189e-01
25%    0.723256  0.447221   0.710465  0.436941      0.72093  4.189189e-01
50%    0.724419  0.495030   0.717442  0.470421      0.72093  4.189189e-01
75%    0.738372  0.551707   0.720930  0.566705      0.72093  4.189189e-01
max    0.746512  0.564470   0.746512  0.620235      0.72093  4.189189e-01

# Checklist

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/checklist/base_offensive_'+str(perc)+'_checklist'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/checklist/base_offensive_'+str(perc)+'_checklist'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/checklist/base_offensive_'+str(perc)+'_checklist'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/checklist/base_offensive_'+str(perc)+'_checklist'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/checklist/base_offensive_'+str(perc)+'_checklist'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_normal(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 4, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  4, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  4, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-10-a91fedf45f9b>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/614 [00:00<?, ?it/s]

Epoch:   0%|          | 0/4 [00:00<?, ?it/s]

Running Epoch 0 of 4:   0%|          | 0/20 [00:00<?, ?it/s]

...

Running Epoch 3 of 4:   0%|          | 0/19 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/860 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/108 [00:00<?, ?it/s]

Roberta
ACC:0.7581395348837209
F1:0.6744700675518285


In [ ]:
data = {'Aug': [ 'eda1', 'eda2', 'eda3', 'eda4','eda5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  eda1  0.656977  0.602251   0.736047  0.659866     0.744186    0.665059
1  eda2  0.781395  0.689421   0.769767  0.612380     0.813953    0.751938
2  eda3  0.705814  0.599559   0.662791  0.593999     0.682558    0.602993
3  eda4  0.763953  0.692302   0.763953  0.714140     0.793023    0.727381
4  eda5  0.723256  0.632146   0.768605  0.713559     0.758140    0.674470

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.726279  0.643136   0.740233  0.658789     0.758372    0.684368
std    0.049214  0.045417   0.045428  0.055714     0.050594    0.058113
min    0.656977  0.599559   0.662791  0.593999     0.682558    0.602993
25%    0.705814  0.602251   0.736047  0.612380     0.744186    0.665059
50%    0.723256  0.632146   0.763953  0.659866     0.758140    0.674470
75%    0.763953  0.689421   0.768605  0.713559     0.793023    0.727381
max    0.781395  0.692302   0.769767  0.714140     0.813953    0.751938

# Back Translation

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/back_translation/base_offensive_'+str(perc)+'_back_translation'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/back_translation/base_offensive_'+str(perc)+'_back_translation'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/back_translation/base_offensive_'+str(perc)+'_back_translation'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/back_translation/base_offensive_'+str(perc)+'_back_translation'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/back_translation/base_offensive_'+str(perc)+'_back_translation'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_normal(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 4, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  4, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  4, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-10-a91fedf45f9b>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/339 [00:00<?, ?it/s]

Epoch:   0%|          | 0/4 [00:00<?, ?it/s]

Running Epoch 0 of 4:   0%|          | 0/11 [00:00<?, ?it/s]

...

Running Epoch 3 of 4:   0%|          | 0/11 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/860 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/108 [00:00<?, ?it/s]

Roberta
ACC:0.7209302325581395
F1:0.4189189189189189


In [ ]:
data = {'Aug': [ 'eda1', 'eda2', 'eda3', 'eda4','eda5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  eda1  0.713953  0.475298   0.727907  0.598689     0.760465    0.660901
1  eda2  0.743023  0.532644   0.720930  0.418919     0.741860    0.523743
2  eda3  0.718605  0.418133   0.720930  0.418919     0.744186    0.610366
3  eda4  0.706977  0.449748   0.719767  0.514749     0.720930    0.418919
4  eda5  0.723256  0.427750   0.723256  0.427750     0.720930    0.418919

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.721163  0.460715   0.722558  0.475805     0.737674    0.526570
std    0.013620  0.045844   0.003247  0.079684     0.016883    0.109832
min    0.706977  0.418133   0.719767  0.418919     0.720930    0.418919
25%    0.713953  0.427750   0.720930  0.418919     0.720930    0.418919
50%    0.718605  0.449748   0.720930  0.427750     0.741860    0.523743
75%    0.723256  0.475298   0.723256  0.514749     0.744186    0.610366
max    0.743023  0.532644   0.727907  0.598689     0.760465    0.660901

# LAMBADA

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/lambada/base_offensive_'+str(perc)+'_lambada'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/lambada/base_offensive_'+str(perc)+'_lambada'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/lambada/base_offensive_'+str(perc)+'_lambada'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/lambada/base_offensive_'+str(perc)+'_lambada'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/lambada/base_offensive_'+str(perc)+'_lambada'+str(i+5)+'.csv',
       ]
borig = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_lambada(arqs[j], borig[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 1, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  1, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  1, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-13-df95bd675bd6>:13: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/1020 [00:00<?, ?it/s]

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/32 [00:00<?, ?it/s]

...

Running Epoch 0 of 1:   0%|          | 0/32 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/860 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/108 [00:00<?, ?it/s]

Roberta
ACC:0.7209302325581395
F1:0.4189189189189189


In [ ]:
data = {'Aug': [ 'eda1', 'eda2', 'eda3', 'eda4','eda5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  eda1   0.72093  0.418919   0.720930  0.418919      0.72093    0.418919
1  eda2   0.72093  0.418919   0.720930  0.418919      0.72093    0.418919
2  eda3   0.72093  0.418919   0.719767  0.422531      0.72093    0.418919
3  eda4   0.72093  0.418919   0.720930  0.418919      0.72093    0.418919
4  eda5   0.72093  0.418919   0.725581  0.496627      0.72093    0.418919

In [ ]:
base_resultados.describe()

BERT_ACC       BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC    ROBERTA_F1
count   5.00000  5.000000e+00   5.000000  5.000000      5.00000  5.000000e+00
mean    0.72093  4.189189e-01   0.721628  0.435183      0.72093  4.189189e-01
std     0.00000  6.206335e-17   0.002267  0.034384      0.00000  6.206335e-17
min     0.72093  4.189189e-01   0.719767  0.418919      0.72093  4.189189e-01
25%     0.72093  4.189189e-01   0.720930  0.418919      0.72093  4.189189e-01
50%     0.72093  4.189189e-01   0.720930  0.418919      0.72093  4.189189e-01
75%     0.72093  4.189189e-01   0.720930  0.422531      0.72093  4.189189e-01
max     0.72093  4.189189e-01   0.725581  0.496627      0.72093  4.189189e-01

# Contrastive LAMBADA

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/lambada/base_offensive_'+str(perc)+'_lambada_contrastive'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/lambada/base_offensive_'+str(perc)+'_lambada_contrastive'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/lambada/base_offensive_'+str(perc)+'_lambada_contrastive'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/lambada/base_offensive_'+str(perc)+'_lambada_contrastive'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/lambada/base_offensive_'+str(perc)+'_lambada_contrastive'+str(i+5)+'.csv',
       ]
borig = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_lambada(arqs[j], borig[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 1, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  1, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  1, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-13-df95bd675bd6>:13: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/1020 [00:00<?, ?it/s]

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/32 [00:00<?, ?it/s]

...

Running Epoch 0 of 1:   0%|          | 0/32 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/860 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/108 [00:00<?, ?it/s]

Roberta
ACC:0.7209302325581395
F1:0.4189189189189189


In [ ]:
data = {'Aug': [ 'eda1', 'eda2', 'eda3', 'eda4','eda5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  eda1  0.727907  0.469863   0.687209  0.567096     0.720930    0.418919
1  eda2  0.723256  0.439319   0.722093  0.423352     0.720930    0.418919
2  eda3  0.720930  0.418919   0.718605  0.418133     0.720930    0.418919
3  eda4  0.724419  0.457913   0.713953  0.420472     0.710465    0.430465
4  eda5  0.724419  0.495943   0.675581  0.577105     0.720930    0.418919

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.724186  0.456391   0.703488  0.481232     0.718837    0.421228
std    0.002521  0.029342   0.020784  0.083048     0.004680    0.005164
min    0.720930  0.418919   0.675581  0.418133     0.710465    0.418919
25%    0.723256  0.439319   0.687209  0.420472     0.720930    0.418919
50%    0.724419  0.457913   0.713953  0.423352     0.720930    0.418919
75%    0.724419  0.469863   0.718605  0.567096     0.720930    0.418919
max    0.727907  0.495943   0.722093  0.577105     0.720930    0.430465

# LLAMA 2 Paraphraser

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/gptparaphrase/base_offensive_'+str(perc)+'_gptparaphrase'+str(i+1)+'.pkl',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/gptparaphrase/base_offensive_'+str(perc)+'_gptparaphrase'+str(i+2)+'.pkl',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/gptparaphrase/base_offensive_'+str(perc)+'_gptparaphrase'+str(i+3)+'.pkl',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/gptparaphrase/base_offensive_'+str(perc)+'_gptparaphrase'+str(i+4)+'.pkl',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/gptparaphrase/base_offensive_'+str(perc)+'_gptparaphrase'+str(i+5)+'.pkl',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_normal_pkl(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 4, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet', 4, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  4, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-12-8a66c1fcd9f8>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/989 [00:00<?, ?it/s]

Epoch:   0%|          | 0/4 [00:00<?, ?it/s]

Running Epoch 0 of 4:   0%|          | 0/31 [00:00<?, ?it/s]

...

Running Epoch 3 of 4:   0%|          | 0/30 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/860 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/108 [00:00<?, ?it/s]

Roberta
ACC:0.7627906976744186
F1:0.7123934426229509


In [ ]:
data = {'Aug': [ 'eda1', 'eda2', 'eda3', 'eda4','eda5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  eda1  0.693023  0.601584   0.737209  0.631894     0.722093    0.614064
1  eda2  0.779070  0.708123   0.765116  0.677637     0.800000    0.732502
2  eda3  0.741860  0.665932   0.594186  0.569738     0.734884    0.698707
3  eda4  0.715116  0.658951   0.759302  0.640055     0.779070    0.703580
4  eda5  0.748837  0.697599   0.767442  0.695508     0.762791    0.712393

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.735581  0.666438   0.724651  0.642966     0.759767    0.692249
std    0.032926  0.041746   0.073905  0.048622     0.031776    0.045577
min    0.693023  0.601584   0.594186  0.569738     0.722093    0.614064
25%    0.715116  0.658951   0.737209  0.631894     0.734884    0.698707
50%    0.741860  0.665932   0.759302  0.640055     0.762791    0.703580
75%    0.748837  0.697599   0.765116  0.677637     0.779070    0.712393
max    0.779070  0.708123   0.767442  0.695508     0.800000    0.732502

# GPTNEOKEY

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/teste_algo/base_offensive_'+str(perc)+'_gptneokey'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/teste_algo/base_offensive_'+str(perc)+'_gptneokey'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/teste_algo/base_offensive_'+str(perc)+'_gptneokey'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/teste_algo/base_offensive_'+str(perc)+'_gptneokey'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/teste_algo/base_offensive_'+str(perc)+'_gptneokey'+str(i+5)+'.csv',
       ]
borig = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/offensive/base_offensive_'+str(perc)+'_original'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_lambada(arqs[j], borig[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 4, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  4, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  4, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-12-df95bd675bd6>:13: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/1020 [00:00<?, ?it/s]

...

Running Epoch 3 of 4:   0%|          | 0/32 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/860 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/108 [00:00<?, ?it/s]

Roberta
ACC:0.763953488372093
F1:0.7299926535978039


In [ ]:
data = {'Aug': [ 'eda1', 'eda2', 'eda3', 'eda4','eda5'], # 'eda1', 'eda2', 'eda3', 'eda4','eda5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  eda1  0.670930  0.647663   0.687209  0.658589     0.672093    0.649132
1  eda2  0.776744  0.733628   0.754651  0.715508     0.823256    0.778667
2  eda3  0.626744  0.607378   0.645349  0.627748     0.729070    0.689502
3  eda4  0.745349  0.711909   0.805814  0.748335     0.827907    0.782191
4  eda5  0.669767  0.647533   0.751163  0.719237     0.763953    0.729993

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.697907  0.669622   0.728837  0.693883     0.763256    0.725897
std    0.061339  0.051791   0.062836  0.049232     0.065688    0.057419
min    0.626744  0.607378   0.645349  0.627748     0.672093    0.649132
25%    0.669767  0.647533   0.687209  0.658589     0.729070    0.689502
50%    0.670930  0.647663   0.751163  0.715508     0.763953    0.729993
75%    0.745349  0.711909   0.754651  0.719237     0.823256    0.778667
max    0.776744  0.733628   0.805814  0.748335     0.827907    0.782191